# Transform IUPAC names into numerical data. Dopamine D1 receptor antagonists.

In [1]:
import pandas as pd

# Upload dataset as data frame
df_cids =pd.read_csv('df1_targets.csv', index_col=[0])

# To avoid truncation of some columns during data frame display
pd.set_option('display.max_columns', None) 

# Display the data frame
print('Shape of the data frame: ', df_cids.shape)
df_cids.head()

Shape of the data frame:  (54899, 2)


UPAC  target
0  [2-[1-(2-methoxyethyl)-2,5-dimethylpyrrol-3-yl...       0
1  4-methyl-N-[[[2-(2-methylphenoxy)acetyl]amino]...       1
2    3-(4-methoxyphenyl)-5-phenylcyclohex-2-en-1-one       0
3  (2Z)-2-(thiophen-2-ylmethylidene)-1-benzothiop...       0
4  2-[4-(4-methylbenzoyl)piperidin-1-yl]-N-(4-met...       0

In [2]:
df_cids = df_cids.dropna()
df_cids.shape

(54899, 2)

In [3]:
df_cids = df_cids.drop_duplicates()
df_cids.shape

(54899, 2)

In [4]:
df_cids = df_cids[df_cids['UPAC'].notna()]
df_cids['UPAC'] = df_cids['UPAC'].astype('string') 
df_cids.dtypes

UPAC      string[python]
target             int64
dtype: object

In [5]:
# make a copy to use latter for connection aiwth smiles 
df_iupac_target = df_cids.copy()

In [6]:
# Obtain listo fo UPAC formulas provided in PubChem
UPAC_list = df_cids['UPAC'].to_list()

for item in UPAC_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

[2-[1-(2-methoxyethyl)-2,5-dimethylpyrrol-3-yl]-2-oxoethyl] 4-(3,5-dimethylpyrazol-1-yl)benzoate
4-methyl-N-[[[2-(2-methylphenoxy)acetyl]amino]carbamothioyl]benzamide
3-(4-methoxyphenyl)-5-phenylcyclohex-2-en-1-one
(2Z)-2-(thiophen-2-ylmethylidene)-1-benzothiophen-3-one
2-[4-(4-methylbenzoyl)piperidin-1-yl]-N-(4-methyl-1,3-thiazol-2-yl)acetamide


In [7]:
from string import digits

# Remove elements from UPAC formulas
dataset = []
for i in UPAC_list:
    # Replace simbols with a coma
    new_list = i.translate(str.maketrans({'[': ' , ', ']': ' , ', 
                                         '(': ' , ', ')' : ' , ',
                                         '-': ' , ', ';' : ' , '}))
    
    new_str = new_list.translate(str.maketrans('', '', digits))
    dataset.append(new_str)
dataset

for item in dataset[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

 ,  ,  ,  ,  ,  , methoxyethyl ,  , , , dimethylpyrrol ,  , yl ,  ,  , oxoethyl ,   ,  , , , dimethylpyrazol ,  , yl , benzoate
 , methyl , N ,  ,  ,  ,  ,  ,  , methylphenoxy , acetyl , amino , carbamothioyl , benzamide
 ,  ,  , methoxyphenyl ,  ,  , phenylcyclohex ,  , en ,  , one
 , Z ,  ,  ,  , thiophen ,  , ylmethylidene ,  ,  , benzothiophen ,  , one
 ,  ,  ,  ,  , methylbenzoyl , piperidin ,  , yl ,  , N ,  ,  , methyl , , , thiazol ,  , yl , acetamide


In [8]:
# Convert the strings into list of strings
new_strings = []
for i in dataset:
    parsed_string = i.split(",")
    new_strings.append(parsed_string)
new_strings

for item in new_strings[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

[' ', '  ', '  ', '  ', '  ', '  ', ' methoxyethyl ', '  ', ' ', ' ', ' dimethylpyrrol ', '  ', ' yl ', '  ', '  ', ' oxoethyl ', '   ', '  ', ' ', ' ', ' dimethylpyrazol ', '  ', ' yl ', ' benzoate']
[' ', ' methyl ', ' N ', '  ', '  ', '  ', '  ', '  ', '  ', ' methylphenoxy ', ' acetyl ', ' amino ', ' carbamothioyl ', ' benzamide']
[' ', '  ', '  ', ' methoxyphenyl ', '  ', '  ', ' phenylcyclohex ', '  ', ' en ', '  ', ' one']
[' ', ' Z ', '  ', '  ', '  ', ' thiophen ', '  ', ' ylmethylidene ', '  ', '  ', ' benzothiophen ', '  ', ' one']
[' ', '  ', '  ', '  ', '  ', ' methylbenzoyl ', ' piperidin ', '  ', ' yl ', '  ', ' N ', '  ', '  ', ' methyl ', ' ', ' ', ' thiazol ', '  ', ' yl ', ' acetamide']


In [9]:
from functools import reduce
# Convert list of lists in one list 
new_list = reduce(lambda a, b: a + b, new_strings)

for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

In [10]:
new_list = [s.replace(' ', '') for s in new_list]
for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

In [11]:
# Print the muber of left strings after reduction
print (len (new_list))

955429


In [12]:
# remove duplicates
from collections import OrderedDict

new_list = list(OrderedDict.fromkeys(new_list)) 

for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)


methoxyethyl
dimethylpyrrol
yl
oxoethyl


In [13]:
# Remove one letter strings
new_list_columns = [x for x in new_list if len(x) >= 4]

for item in new_list_columns[:5]:   # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

methoxyethyl
dimethylpyrrol
oxoethyl
dimethylpyrazol
benzoate


In [14]:
print (len (new_list_columns))

4609


In [15]:
new_list_columns.sort()
new_list_columns

['acenaphthylene',
 'acenaphthyleno',
 'acetamide',
 'acetamido',
 'acetamidoacetate',
 'acetamidoacetyl',
 'acetamidoadamantane',
 'acetamidoanilino',
 'acetamidobenzenesulfonate',
 'acetamidobenzoate',
 'acetamidobenzoyl',
 'acetamidocarbamothioyl',
 'acetamidoethyl',
 'acetamidoethylN',
 'acetamidoethylamino',
 'acetamidoethylsulfanyl',
 'acetamidophenoxy',
 'acetamidophenyl',
 'acetamidopropanoate',
 'acetamidopyridin',
 'acetamidopyridine',
 'acetamidothiadiazole',
 'acetate',
 'aceticacid',
 'acetohydrazide',
 'acetonitrile',
 'acetyl',
 'acetylanilino',
 'acetylbenzo',
 'acetylcarbamothioylamino',
 'acetylcarbamoylamino',
 'acetylhydrazinylidene',
 'acetylindol',
 'acetylindolizine',
 'acetyloxy',
 'acetyloxybenzoyl',
 'acetyloxymethyl',
 'acetyloxyphenyl',
 'acetyloxypropan',
 'acetyloxyquinolin',
 'acetylphenoxy',
 'acetylphenyl',
 'acetylpiperazin',
 'acetylpiperazine',
 'acetylpiperidin',
 'acetylsulfamoyl',
 'acetylsulfanylacetyl',
 'acetylthiophen',
 'acridin',
 'acridine'

In [16]:
import numpy as np

dict_func_groups = dict.fromkeys(new_list_columns, 0)
dict_func_groups

{'acenaphthylene': 0,
 'acenaphthyleno': 0,
 'acetamide': 0,
 'acetamido': 0,
 'acetamidoacetate': 0,
 'acetamidoacetyl': 0,
 'acetamidoadamantane': 0,
 'acetamidoanilino': 0,
 'acetamidobenzenesulfonate': 0,
 'acetamidobenzoate': 0,
 'acetamidobenzoyl': 0,
 'acetamidocarbamothioyl': 0,
 'acetamidoethyl': 0,
 'acetamidoethylN': 0,
 'acetamidoethylamino': 0,
 'acetamidoethylsulfanyl': 0,
 'acetamidophenoxy': 0,
 'acetamidophenyl': 0,
 'acetamidopropanoate': 0,
 'acetamidopyridin': 0,
 'acetamidopyridine': 0,
 'acetamidothiadiazole': 0,
 'acetate': 0,
 'aceticacid': 0,
 'acetohydrazide': 0,
 'acetonitrile': 0,
 'acetyl': 0,
 'acetylanilino': 0,
 'acetylbenzo': 0,
 'acetylcarbamothioylamino': 0,
 'acetylcarbamoylamino': 0,
 'acetylhydrazinylidene': 0,
 'acetylindol': 0,
 'acetylindolizine': 0,
 'acetyloxy': 0,
 'acetyloxybenzoyl': 0,
 'acetyloxymethyl': 0,
 'acetyloxyphenyl': 0,
 'acetyloxypropan': 0,
 'acetyloxyquinolin': 0,
 'acetylphenoxy': 0,
 'acetylphenyl': 0,
 'acetylpiperazin': 0,

In [17]:
# https://stackoverflow.com/questions/28056171/how-to-build-and-fill-pandas-dataframe-from-for-loop
import copy
import re
dataset = []
data = []
# new_strings = []

list_formulas = df_cids['UPAC'].to_list()
for formula in list_formulas:
    new_list = re.findall(r'\b\w{4,}\b', formula)
    for group in new_list:
        # working
        new_dict = copy.deepcopy(dict_func_groups)
        for ii in new_list:
            if ii in new_dict.keys():
                new_dict[ii] +=1
                    
    id = formula
    # Combine all new features in an array
    # arr =[id, new_dict.values()]
    dataset.append(new_dict.values())

In [18]:
# Create an "index" column with the corresponding index values
df_iupac_target['index'] = df_iupac_target.index

# Display df_similarity
print('Shape of df_iupac_target ', df_iupac_target.shape)
df_iupac_target.head() 

Shape of df_iupac_target  (54899, 3)


UPAC  target  index
0  [2-[1-(2-methoxyethyl)-2,5-dimethylpyrrol-3-yl...       0      0
1  4-methyl-N-[[[2-(2-methylphenoxy)acetyl]amino]...       1      1
2    3-(4-methoxyphenyl)-5-phenylcyclohex-2-en-1-one       0      2
3  (2Z)-2-(thiophen-2-ylmethylidene)-1-benzothiop...       0      3
4  2-[4-(4-methylbenzoyl)piperidin-1-yl]-N-(4-met...       0      4

In [19]:
df_func_groups = pd.DataFrame.from_dict(dataset,
                                        orient='columns',
                                        dtype=None, columns=None) 


df_func_groups.columns = new_list_columns
df_func_groups.head()

acenaphthylene  acenaphthyleno  acetamide  acetamido  acetamidoacetate  \
0               0               0          0          0                 0   
1               0               0          0          0                 0   
2               0               0          0          0                 0   
3               0               0          0          0                 0   
4               0               0          1          0                 0   

   acetamidoacetyl  acetamidoadamantane  acetamidoanilino  \
0                0                    0                 0   
1                0                    0                 0   
2                0                    0                 0   
3                0                    0                 0   
4                0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidocarbamothioyl  acetamidoethyl  acetamidoethylN  \
0                       0               0                0   
1                       0               0                0   
2                       0               0                0   
3                       0               0                0   
4                       0               0                0   

   acetamidoethylamino  acetamidoethylsulfanyl  acetamidophenoxy  \
0                    0                       0                 0   
1                    0                       0                 0   
2                    0                       0                 0   
3                    0                       0                 0   
4                    0                       0                 0   

   acetamidophenyl  acetamidopropanoate  acetamidopyridin  acetamidopyridine  \
0                0                    0                 0                  0   
1                0                    0                 0                  0   
2                0                    0                 0                  0   
3                0                    0                 0                  0   
4                0                    0                 0                  0   

   acetamidothiadiazole  acetate  aceticacid  acetohydrazide  acetonitrile  \
0                     0        0           0               0             0   
1                     0        0           0               0             0   
2                     0        0           0               0             0   
3                     0        0           0               0             0   
4                     0        0           0               0             0   

   acetyl  acetylanilino  acetylbenzo  acetylcarbamothioylamino  \
0       0              0            0                         0   
1       1              0            0                         0   
2       0              0            0                         0   
3       0              0            0                         0   
4       0              0            0                         0   

   acetylcarbamoylamino  acetylhydrazinylidene  acetylindol  acetylindolizine  \
0                     0                      0            0                 0   
1                     0                      0            0                 0   
2                     0                      0            0                 0   
3                     0                      0            0                 0   
4                     0                      0            0                 0   

   acetyloxy  acetyloxybenzoyl  acetyloxymethyl  acetyloxyphenyl  \
0          0                 0                0                0   


In [20]:
# Create an "index" column with the corresponding index values
df_func_groups['index'] = df_func_groups.index

# Convert the index values into strings
# df_func_groups['index'] = df_func_groups['index'].astype(str)

# Display df_similarity
print('Shape of df_func_groups: ', df_func_groups.shape)
df_func_groups.head() 

Shape of df_func_groups:  (54899, 4610)


acenaphthylene  acenaphthyleno  acetamide  acetamido  acetamidoacetate  \
0               0               0          0          0                 0   
1               0               0          0          0                 0   
2               0               0          0          0                 0   
3               0               0          0          0                 0   
4               0               0          1          0                 0   

   acetamidoacetyl  acetamidoadamantane  acetamidoanilino  \
0                0                    0                 0   
1                0                    0                 0   
2                0                    0                 0   
3                0                    0                 0   
4                0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidocarbamothioyl  acetamidoethyl  acetamidoethylN  \
0                       0               0                0   
1                       0               0                0   
2                       0               0                0   
3                       0               0                0   
4                       0               0                0   

   acetamidoethylamino  acetamidoethylsulfanyl  acetamidophenoxy  \
0                    0                       0                 0   
1                    0                       0                 0   
2                    0                       0                 0   
3                    0                       0                 0   
4                    0                       0                 0   

   acetamidophenyl  acetamidopropanoate  acetamidopyridin  acetamidopyridine  \
0                0                    0                 0                  0   
1                0                    0                 0                  0   
2                0                    0                 0                  0   
3                0                    0                 0                  0   
4                0                    0                 0                  0   

   acetamidothiadiazole  acetate  aceticacid  acetohydrazide  acetonitrile  \
0                     0        0           0               0             0   
1                     0        0           0               0             0   
2                     0        0           0               0             0   
3                     0        0           0               0             0   
4                     0        0           0               0             0   

   acetyl  acetylanilino  acetylbenzo  acetylcarbamothioylamino  \
0       0              0            0                         0   
1       1              0            0                         0   
2       0              0            0                         0   
3       0              0            0                         0   
4       0              0            0                         0   

   acetylcarbamoylamino  acetylhydrazinylidene  acetylindol  acetylindolizine  \
0                     0                      0            0                 0   
1                     0                      0            0                 0   
2                     0                      0            0                 0   
3                     0                      0            0                 0   
4                     0                      0            0                 0   

   acetyloxy  acetyloxybenzoyl  acetyloxymethyl  acetyloxyphenyl  \
0          0                 0                0                0   


In [21]:
# Add the new data frame df_similarity to the already existing df based on "index"
df = pd.merge(df_iupac_target,df_func_groups, on=['index'])

# Display df_similarity
print('Shape of df: ', df.shape)
df.head()

Shape of df:  (54899, 4612)


UPAC  target  index  \
0  [2-[1-(2-methoxyethyl)-2,5-dimethylpyrrol-3-yl...       0      0   
1  4-methyl-N-[[[2-(2-methylphenoxy)acetyl]amino]...       1      1   
2    3-(4-methoxyphenyl)-5-phenylcyclohex-2-en-1-one       0      2   
3  (2Z)-2-(thiophen-2-ylmethylidene)-1-benzothiop...       0      3   
4  2-[4-(4-methylbenzoyl)piperidin-1-yl]-N-(4-met...       0      4   

   acenaphthylene  acenaphthyleno  acetamide  acetamido  acetamidoacetate  \
0               0               0          0          0                 0   
1               0               0          0          0                 0   
2               0               0          0          0                 0   
3               0               0          0          0                 0   
4               0               0          1          0                 0   

   acetamidoacetyl  acetamidoadamantane  acetamidoanilino  \
0                0                    0                 0   
1                0                    0                 0   
2                0                    0                 0   
3                0                    0                 0   
4                0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidocarbamothioyl  acetamidoethyl  acetamidoethylN  \
0                       0               0                0   
1                       0               0                0   
2                       0               0                0   
3                       0               0                0   
4                       0               0                0   

   acetamidoethylamino  acetamidoethylsulfanyl  acetamidophenoxy  \
0                    0                       0                 0   
1                    0                       0                 0   
2                    0                       0                 0   
3                    0                       0                 0   
4                    0                       0                 0   

   acetamidophenyl  acetamidopropanoate  acetamidopyridin  acetamidopyridine  \
0                0                    0                 0                  0   
1                0                    0                 0                  0   
2                0                    0                 0                  0   
3                0                    0                 0                  0   
4                0                    0                 0                  0   

   acetamidothiadiazole  acetate  aceticacid  acetohydrazide  acetonitrile  \
0                     0        0           0               0             0   
1                     0        0           0               0             0   
2                     0        0           0               0             0   
3                     0        0           0               0             0   
4                     0        0           0               0             0   

   acetyl  acetylanilino  acetylbenzo  acetylcarbamothioylamino  \
0       0              0            0                         0   
1       1              0            0                         0   
2       0              0            0                         0   
3       0              0            0                         0   
4       0              0            0                         0   

   acetylcarbamoylamino  acetylhydrazinylidene  acetylindol  acetylindolizine  \
0                     0                      0            0                 0   
1                     0                      0            0                 0  

In [22]:
df.to_csv('df1_for_final.csv')

In [23]:
# Drop the CID and UPAC columns by name
df = df.drop(columns=['UPAC', 'index'],axis=1) 

In [24]:
# Display the data frame
print('Shape of the data frame: ', df.shape)
df.head()

Shape of the data frame:  (54899, 4610)


target  acenaphthylene  acenaphthyleno  acetamide  acetamido  \
0       0               0               0          0          0   
1       1               0               0          0          0   
2       0               0               0          0          0   
3       0               0               0          0          0   
4       0               0               0          1          0   

   acetamidoacetate  acetamidoacetyl  acetamidoadamantane  acetamidoanilino  \
0                 0                0                    0                 0   
1                 0                0                    0                 0   
2                 0                0                    0                 0   
3                 0                0                    0                 0   
4                 0                0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidocarbamothioyl  acetamidoethyl  acetamidoethylN  \
0                       0               0                0   
1                       0               0                0   
2                       0               0                0   
3                       0               0                0   
4                       0               0                0   

   acetamidoethylamino  acetamidoethylsulfanyl  acetamidophenoxy  \
0                    0                       0                 0   
1                    0                       0                 0   
2                    0                       0                 0   
3                    0                       0                 0   
4                    0                       0                 0   

   acetamidophenyl  acetamidopropanoate  acetamidopyridin  acetamidopyridine  \
0                0                    0                 0                  0   
1                0                    0                 0                  0   
2                0                    0                 0                  0   
3                0                    0                 0                  0   
4                0                    0                 0                  0   

   acetamidothiadiazole  acetate  aceticacid  acetohydrazide  acetonitrile  \
0                     0        0           0               0             0   
1                     0        0           0               0             0   
2                     0        0           0               0             0   
3                     0        0           0               0             0   
4                     0        0           0               0             0   

   acetyl  acetylanilino  acetylbenzo  acetylcarbamothioylamino  \
0       0              0            0                         0   
1       1              0            0                         0   
2       0              0            0                         0   
3       0              0            0                         0   
4       0              0            0                         0   

   acetylcarbamoylamino  acetylhydrazinylidene  acetylindol  acetylindolizine  \
0                     0                      0            0                 0   
1                     0                      0            0                 0   
2                     0                      0            0                 0   
3                     0                      0            0                 0   
4                     0                      0            0                 0   

   acetyloxy  acetyloxybenzoyl  acetyloxymethyl  acetyloxyphenyl  \
0          0        

In [25]:
df.to_csv('df1_targets_IUPACs.csv')